<a href="https://colab.research.google.com/github/PondKann/KKU_data_mining/blob/master/Project_Mining_Zoo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Association และ K-Nearest Neighbors
- Association เป็นการดูรูปแบบของข้อมูลว่าถ้ามีลักษณะนี้ แล้วจะเกิดลักษณะใดตามมา โดยกำหนดให้ Transection คือ ชื่อสัตว์ และ Feature คือ ลักษณะทั้ง 16 ลักษณะของสัตว์
- KNN ทำขึ้นเพื่อทำนายประเภทของสัตว์จากลักษณะทั้ง 16 ลักษณะของสัตว์

### ข้อมูล
- https://www.kaggle.com/uciml/zoo-animal-classification?select=zoo.csv&fbclid=IwAR19ybeDlNDWZ0uthvV0srz4Rs44fiheUCsGhUgOIIgDLphGEAjnNPPvSfA

ข้อมูลชุดนี้เป็นข้อมูลของสัตว์ในสวนสัตว์ โดยจะประกอบไปด้วย สัตว์ 101 ตัว มีตัวแปร 16 ตัว ที่อธิบายลักษณะต่าง ๆ ของสัตว์ ดังนี้ ​

hair(ผม), heathers(ขน), eggs(ไข่), milk(นม), airborne(ปีก), aquatic(อยู่ในน้ำ), predator(นักล่า), toothed(ฟัน), backbone(กระดูกสันหลัง), breathes(ใช้จมูกหายใจ), venomous(มีพิษ), fins(ครีบ), legs(ขา), tail(หาง), domestic(ในประเทศ) และ catsize(ใบหู)​

ซึ่งสามารถแบ่งประเภทของสัตว์ออกเป็น 7 ประเภท ได้แก่  Mammal(สัตว์เลี้ยงลูกด้วยนม), Bird(นก), Reptile(สัตว์เลื้อยคลาน), Fish(ปลา), Amphibian(สัตว์สะเทินน้ำสะเทินบก), Bug(แมลง) และInvertebrate(สัตว์ไม่มีกระดูกสันหลัง)


### เรียกใช้ไฟล์ 

เชื่อมต่อ Google Drive ของเราเข้ากับ Google Colab

In [ ]:
from google.colab import drive 
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


การเชื่อมต่อข้อมูลที่อยู่ใน Google Drive ให้มาอยู่ในตัวแปลที่ชื่อ path

In [ ]:
path = '/content/drive/My Drive/DataMining_Project'

เรียกดูไฟล์ข้อมูลที่อยู่ใน Google Drive ที่ได้เชื่อมต่อไว้

In [ ]:
import os

In [ ]:
os.listdir(path)

['zoo.csv', 'class.csv']

การ join ไฟล์ข้อมูล กับ path และทำการอ่านไฟล์ข้อมูล ตั้งชื่อให้อยู่ในตัวแปล ชื่อ zoo_type_df และ class_type_df

In [ ]:
import os
import pandas as pd
zoo_type = os.path.join(path,'zoo.csv')  
class_type = os.path.join(path,'class.csv')
zoo_type_df = pd.read_csv(zoo_type)
class_type_df = pd.read_csv(class_type)

เรียกดูข้อมูล

จะเห็นได้ว่าใน Dataframe ที่ชื่อว่า zoo_type_df มี ข้อมูลทั้งหมด 101 แถว และ 18 คอลัมน์


In [ ]:
zoo_type_df

animal_name  hair  feathers  eggs  ...  tail  domestic  catsize  class_type
0      aardvark     1         0     0  ...     0         0        1           1
1      antelope     1         0     0  ...     1         0        1           1
2          bass     0         0     1  ...     1         0        0           4
3          bear     1         0     0  ...     0         0        1           1
4          boar     1         0     0  ...     1         0        1           1
..          ...   ...       ...   ...  ...   ...       ...      ...         ...
96      wallaby     1         0     0  ...     1         0        1           1
97         wasp     1         0     1  ...     0         0        0           6
98         wolf     1         0     0  ...     1         0        1           1
99         worm     0         0     1  ...     0         0        0           7
100        wren     0         1     1  ...     1         0        0           2

[101 rows x 18 columns]

จะเห็นได้ว่าใน Dataframe ที่ชื่อว่า class_type_df มี ข้อมูลทั้งหมด 7 แถว และ 4 คอลัมน์

In [ ]:
class_type_df

Class_Number  ...                                        Animal_Name
0             1  ...  aardvark, antelope, bear, boar, buffalo, calf,...
1             2  ...  chicken, crow, dove, duck, flamingo, gull, haw...
2             3  ...    pitviper, seasnake, slowworm, tortoise, tuatara
3             4  ...  bass, carp, catfish, chub, dogfish, haddock, h...
4             5  ...                             frog, frog, newt, toad
5             6  ...  flea, gnat, honeybee, housefly, ladybird, moth...
6             7  ...  clam, crab, crayfish, lobster, octopus, scorpi...

[7 rows x 4 columns]

## ทำการเเตรียมข้อมูล สำหรับทำ Association

In [ ]:
from pandas.api.types import CategoricalDtype

###แบ่งกลุ่มลักษณะของสัตว์ทั้งหมด 16 ลักษณะ จากไฟล์ข้อมูล zoo_type_df

ให้ข้อมูลที่อยู่ใน zoo_type_df ตัวในตัวแปลใหม่ที่ชื่อว่า zoo_type เพื่อนำไปแปลงข้อมูลให้สามารถนำไปทำ Association ได้

In [ ]:
zoo_type1 = zoo_type_df

การแบ่งข้อมูลออกเป็นกลุ่มตามช่วงของค่าแบ่งที่เราได้กำหนดไว้ 

โดยจะแบ่งแค่คอลัมน์ที่เป็นลักษณะของสัตว์ ได้แก่ hair(ผม), heathers(ขน), eggs(ไข่), milk(นม), airborne(ในอากาศ), aquatic(อยู่ในน้ำ), predator(นักล่า), toothed(ฟัน), backbone(กระดูกสันหลัง), breathes(ใช้จมูกหายใจ), venomous(มีพิษ), fins(ครีบ), legs(ขา), tail(หาง), domestic(ในประเทศ) และ catsize(ใบหู)​

In [ ]:
h_bucket = ['nohair','hair']      #ข้อมูลที่จะถูกนำไปเติมในคอลัมน์ใหม่
zoo_type1['hair_group'] = pd.cut(zoo_type1.hair,      #เพิ่มคอลัมน์ hair_group ในตาราง zoo_type1 โดยทำการแบ่งจากข้อมูลที่อยู่ในคอลัมน์ hair
                            bins=[0,1,2],     #กำหนดช่วงของข้อมูลที่จะทำการแบ่ง 
                            labels=h_bucket,      #ข้อมูลที่จะนำมาเติมอยู่ใน h_bucket นั่นคือ nohair และ hair
                            right=False).astype(str).astype(CategoricalDtype(h_bucket,ordered=True))      
                            #right = False คือ ให้แบ่งข้อมูลจาก เริ่มจาก เลข ที่อยู่ซ้าย ไปจนถึง เลข ที่ยังไม่ถึง เลขที่อยู่ขวา เช่น 0,1 คือ เริ่มจาก 0 ไปถึง 0.99 ซึ่งจะยังไม่ถึง 1 โดยจะให้ค่าที่อยู่ในช่วงนี้ แทนด้วย nohair

In [ ]:
f_bucket = ['nofeathers','feathers']
zoo_type1['feathers_group'] = pd.cut(zoo_type1.feathers,
                            bins=[0,1,2],
                            labels=f_bucket,
                            right=False).astype(str).astype(CategoricalDtype(f_bucket,ordered=True))

In [ ]:
e_bucket = ['noeggs','eggs']
zoo_type1['eggs_group'] = pd.cut(zoo_type1.eggs,
                            bins=[0,1,2],
                            labels=e_bucket,
                            right=False).astype(str).astype(CategoricalDtype(e_bucket,ordered=True))

In [ ]:
m_bucket = ['nomilk','milk']
zoo_type1['milk_group'] = pd.cut(zoo_type1.milk,
                            bins=[0,1,2],
                            labels=m_bucket,
                            right=False).astype(str).astype(CategoricalDtype(m_bucket,ordered=True))

In [ ]:
a_bucket = ['noairborne','airborne']
zoo_type1['airborne_group'] = pd.cut(zoo_type1.airborne,
                            bins=[0,1,2],
                            labels=a_bucket,
                            right=False).astype(str).astype(CategoricalDtype(a_bucket,ordered=True))

In [ ]:
a_bucket = ['noaquatic','aquatic']
zoo_type1['aquatic_group'] = pd.cut(zoo_type1.aquatic,
                            bins=[0,1,2],
                            labels=a_bucket,
                            right=False).astype(str).astype(CategoricalDtype(a_bucket,ordered=True))

In [ ]:
p_bucket = ['nopredator','predator']
zoo_type1['predator_group'] = pd.cut(zoo_type1.predator,
                            bins=[0,1,2],
                            labels=p_bucket,
                            right=False).astype(str).astype(CategoricalDtype(p_bucket,ordered=True))

In [ ]:
t_bucket = ['notoothed','toothed']
zoo_type1['toothed_group'] = pd.cut(zoo_type1.toothed,
                            bins=[0,1,2],
                            labels=t_bucket,
                            right=False).astype(str).astype(CategoricalDtype(t_bucket,ordered=True))

In [ ]:
b_bucket = ['nobackbone','backbone']
zoo_type1['backbone_group'] = pd.cut(zoo_type1.backbone,
                            bins=[0,1,2],
                            labels=b_bucket,
                            right=False).astype(str).astype(CategoricalDtype(b_bucket,ordered=True))

In [ ]:
b_bucket = ['nobreathes','breathes']
zoo_type1['breathes_group'] = pd.cut(zoo_type1.breathes,
                            bins=[0,1,2],
                            labels=b_bucket,
                            right=False).astype(str).astype(CategoricalDtype(b_bucket,ordered=True))

In [ ]:
v_bucket = ['novenomous','venomous']
zoo_type1['venomous_group'] = pd.cut(zoo_type1.venomous,
                            bins=[0,1,2],
                            labels=v_bucket,
                            right=False).astype(str).astype(CategoricalDtype(v_bucket,ordered=True))

In [ ]:
f_bucket = ['nofins','fins']
zoo_type1['fins_group'] = pd.cut(zoo_type1.	fins,
                            bins=[0,1,2],
                            labels=f_bucket,
                            right=False).astype(str).astype(CategoricalDtype(f_bucket,ordered=True))

In [ ]:
l_bucket = ['nolegs','2legs','4legs','6legs','8legs']
zoo_type1['legs_group'] = pd.cut(zoo_type1.	legs,
                            bins=[0,2,4,6,7,9],
                            labels=l_bucket,
                            right=False).astype(str).astype(CategoricalDtype(l_bucket,ordered=True))

In [ ]:
t_bucket = ['notail','tail']
zoo_type1['tail_group'] = pd.cut(zoo_type1.tail,
                            bins=[0,1,2],
                            labels=t_bucket,
                            right=False).astype(str).astype(CategoricalDtype(t_bucket,ordered=True))
zoo_type1

ValueError: ignored

### เนื่องจากคอลัมลักษณะ tail เกิด Error Input array must be 1 dimensional จึงทำการวนลูปค่า 


วนลูปเพื่อเติมข้อมูล เริ่มจาก i ไปจนถึง ความยาวของ zoo_type1

ถ้า ข้อมูลตัวที่ i ของ คอลัมน์ tail = 0 ให้ เติมค่า notail ลงใน ข้อมูลตัวที่ i ของ คอลัมน์ tail_group 

ถ้าข้อมูล ไม่ = 0  (เป็น 1 )ให้ เติมค่า tail ลงใน ข้อมูลตัวที่ i ของ คอลัมน์ tail_group 

In [ ]:
for i in range(len(zoo_type1)):
  if zoo_type1['tail'][i] == 0:
    zoo_type1['tail_group'] = 'notail'
  else:
    zoo_type1['tail_group'] = 'tail'

In [ ]:
d_bucket = ['nodomestic','domestic']
zoo_type1['domestic_group'] = pd.cut(zoo_type1.domestic,
                            bins=[0,1,2],
                            labels=d_bucket,
                            right=False).astype(str).astype(CategoricalDtype(d_bucket,ordered=True))

In [ ]:
c_bucket = ['nocatsize','catsize']
zoo_type1['catsize_group'] = pd.cut(zoo_type1.catsize,
                            bins=[0,1,2],
                            labels=c_bucket,
                            right=False).astype(str).astype(CategoricalDtype(c_bucket,ordered=True))

หลังจากเพิ่มคอลัมน์ครบทุกตัวแล้วจะได้ข้อมูลดังตาราง zoo_type1 มี 101 แถว 34 คอลัมน์ จะเห็นว่า คอลัมน์จะเพิ่มขึ้นมา 16 คอลัมน์จากการแบ่งข้อมูล

In [ ]:
zoo_type1

animal_name  hair  feathers  ...  tail_group  domestic_group  catsize_group
0      aardvark     1         0  ...        tail      nodomestic        catsize
1      antelope     1         0  ...        tail      nodomestic        catsize
2          bass     0         0  ...        tail      nodomestic      nocatsize
3          bear     1         0  ...        tail      nodomestic        catsize
4          boar     1         0  ...        tail      nodomestic        catsize
..          ...   ...       ...  ...         ...             ...            ...
96      wallaby     1         0  ...        tail      nodomestic        catsize
97         wasp     1         0  ...        tail      nodomestic      nocatsize
98         wolf     1         0  ...        tail      nodomestic        catsize
99         worm     0         0  ...        tail      nodomestic      nocatsize
100        wren     0         1  ...        tail      nodomestic      nocatsize

[101 rows x 34 columns]

จาก zoo_type1 ดึงข้อมูลมาเฉพาะ คอลัมน์ที่เราต้องการ นั่นคือ animal_name และ ลักษณะทั้ง 16 ลักษณะ  ให้อยู่ในตัวแปลชื่อ zoo_type2

In [ ]:
zoo_type2 = zoo_type1[['animal_name','hair_group','feathers_group', 'eggs_group', 'milk_group', 'airborne_group', 'aquatic_group', 'predator_group', 'toothed_group', 'backbone_group', 'breathes_group', 'venomous_group', 'fins_group', 'legs_group','tail_group', 'domestic_group', 'catsize_group' ]]
zoo_type2

animal_name hair_group  ... domestic_group catsize_group
0      aardvark       hair  ...     nodomestic       catsize
1      antelope       hair  ...     nodomestic       catsize
2          bass     nohair  ...     nodomestic     nocatsize
3          bear       hair  ...     nodomestic       catsize
4          boar       hair  ...     nodomestic       catsize
..          ...        ...  ...            ...           ...
96      wallaby       hair  ...     nodomestic       catsize
97         wasp       hair  ...     nodomestic     nocatsize
98         wolf       hair  ...     nodomestic       catsize
99         worm     nohair  ...     nodomestic     nocatsize
100        wren     nohair  ...     nodomestic     nocatsize

[101 rows x 17 columns]

In [ ]:
zoo_type2.isnull().any().any()      #เป็นการเช็คว่า isnull หรือไม่ จะเห็นว่าจากข้อมูลนี้ ไม่มีค่า null

False

In [ ]:
#Convert data to list
transacs = []     #กำหนดให้ค่าใน transacs เป็น list ว่าง
for i in range(0,len(zoo_type2)):     # i เริ่มตั้งแต่ 0 ถึง 100 
  transacs.append([str(zoo_type2.values[i,j]) for j in range(1,17)])      #zoo_type2.values เป็นการดูข้อมูลตามคอลัมน์
transacs

# Association ของแต่ละลักษณะ

In [ ]:
!pip install apyori
import numpy as np
import matplotlib.pyplot as plt
from apyori import apriori

In [ ]:
zoo_type1

animal_name  hair  feathers  ...  tail_group  domestic_group  catsize_group
0      aardvark     1         0  ...        tail      nodomestic        catsize
1      antelope     1         0  ...        tail      nodomestic        catsize
2          bass     0         0  ...        tail      nodomestic      nocatsize
3          bear     1         0  ...        tail      nodomestic        catsize
4          boar     1         0  ...        tail      nodomestic        catsize
..          ...   ...       ...  ...         ...             ...            ...
96      wallaby     1         0  ...        tail      nodomestic        catsize
97         wasp     1         0  ...        tail      nodomestic      nocatsize
98         wolf     1         0  ...        tail      nodomestic        catsize
99         worm     0         0  ...        tail      nodomestic      nocatsize
100        wren     0         1  ...        tail      nodomestic      nocatsize

[101 rows x 34 columns]

### ทำการดึงตารางที่ต้องการออกมาให้อยู่ในตัวแปร zoo_type2 

In [ ]:
zoo_type2 = zoo_type1[['animal_name','hair_group','feathers_group', 'eggs_group', 'milk_group', 'airborne_group', 'aquatic_group', 'predator_group', 'toothed_group', 'backbone_group', 'breathes_group', 'venomous_group', 'fins_group', 'legs_group','tail_group', 'domestic_group', 'catsize_group' ]]
zoo_type2

animal_name hair_group  ... domestic_group catsize_group
0      aardvark       hair  ...     nodomestic       catsize
1      antelope       hair  ...     nodomestic       catsize
2          bass     nohair  ...     nodomestic     nocatsize
3          bear       hair  ...     nodomestic       catsize
4          boar       hair  ...     nodomestic       catsize
..          ...        ...  ...            ...           ...
96      wallaby       hair  ...     nodomestic       catsize
97         wasp       hair  ...     nodomestic     nocatsize
98         wolf       hair  ...     nodomestic       catsize
99         worm     nohair  ...     nodomestic     nocatsize
100        wren     nohair  ...     nodomestic     nocatsize

[101 rows x 17 columns]

In [ ]:
zoo_type2.isnull().any().any()

False

In [ ]:
#Convert data to list
transacs = []                                                                                 #กำหนดให้ transacs เป็น list ว่าง สำหรับนำข้อมูลมาใส่
for i in range(0,len(zoo_type2)):                                                     # range(0,len(zoo_type2)) คือ แถวที่ 0 ถึง 100 ของตาราง zoo_type2
  transacs.append([str(zoo_type2.values[i,j]) for j in range(1,17)])      #zoo_type2.values เป็นการดูข้อมูลเรียงตาคอลัมน์ คือ คอลัมน์ที่ 1 ถึง 17   .append คือการเพิ่มข้อมูลเข้าไปใน list
transacs                                                                                        #จะได้ list ที่แยกแต่ละ transection (สัตว์แต่ละตัว)

 Association เพื่อหารูปแบบ

In [ ]:
asso = list(apriori(transacs,min_support = 0.8, min_confidence = 0.7))
asso

[RelationRecord(items=frozenset({'backbone'}), support=0.8217821782178217, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'backbone'}), confidence=0.8217821782178217, lift=1.0)]),
 RelationRecord(items=frozenset({'nodomestic'}), support=0.8712871287128713, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nodomestic'}), confidence=0.8712871287128713, lift=1.0)]),
 RelationRecord(items=frozenset({'nofeathers'}), support=0.801980198019802, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nofeathers'}), confidence=0.801980198019802, lift=1.0)]),
 RelationRecord(items=frozenset({'nofins'}), support=0.8316831683168316, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nofins'}), confidence=0.8316831683168316, lift=1.0)]),
 RelationRecord(items=frozenset({'novenomous'}), support=0.9207920792079208, ordered_statistics=[OrderedStatistic(items_base=frozenset(), 

### สัตว์ที่ไม่มีพิษ จะมีโอกาสที่จะมีหางด้วยเป็น 100%
### และจะเห็นว่าลักษณะสัตว์ที่ไม่มีพิษ มีโอกาสที่จะมีหางด้วยอยู่ที่ 92.08 %  
### lift เท่ากับ 1 คือ ลักษณะทั้งสองมีความสัมพันธ์กัน


# Association ของแต่ละประเภท

### ดึงส่วนของข้อมูลที่ทำการเปลี่ยนค่าแล้วออกมา

In [ ]:
class_zoo = zoo_type1[['class_type','animal_name','hair_group','feathers_group', 'eggs_group', 'milk_group', 'airborne_group', 'aquatic_group', 'predator_group', 'toothed_group', 'backbone_group', 'breathes_group', 'venomous_group', 'fins_group', 'legs_group','tail_group', 'domestic_group', 'catsize_group' ]]
class_zoo.head()

class_type animal_name hair_group  ... tail_group domestic_group catsize_group
0           1    aardvark       hair  ...       tail     nodomestic       catsize
1           1    antelope       hair  ...       tail     nodomestic       catsize
2           4        bass     nohair  ...       tail     nodomestic     nocatsize
3           1        bear       hair  ...       tail     nodomestic       catsize
4           1        boar       hair  ...       tail     nodomestic       catsize

[5 rows x 18 columns]

### ทำการรวมตาราง

In [ ]:
class_z_merged = class_zoo.merge(class_type_df,how='left',left_on='class_type',right_on='Class_Number')
class_z_merged.head()

class_type  ...                                        Animal_Name
0           1  ...  aardvark, antelope, bear, boar, buffalo, calf,...
1           1  ...  aardvark, antelope, bear, boar, buffalo, calf,...
2           4  ...  bass, carp, catfish, chub, dogfish, haddock, h...
3           1  ...  aardvark, antelope, bear, boar, buffalo, calf,...
4           1  ...  aardvark, antelope, bear, boar, buffalo, calf,...

[5 rows x 22 columns]

### ตัดตารางบางส่วนที่ไม่ได้ใช้ออก

In [ ]:
class_z_merged_dr = class_z_merged.drop(['Class_Number','Number_Of_Animal_Species_In_Class','class_type','animal_name','Animal_Name'],axis=1)
class_z_merged_dr.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
0       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
1       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
2     nohair     nofeathers       eggs  ...     nodomestic     nocatsize       Fish
3       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
4       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal

[5 rows x 17 columns]

## Association ของสัตว์ประเภท Mammal

### ทำการเลือกข้อมูลสัตว์ประเภท Mammal จากคอลัม Class Type ออกมา

In [ ]:
class_Mammal = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Mammal']
class_Mammal.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
0       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
1       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
3       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
4       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal
5       hair     nofeathers     noeggs  ...     nodomestic       catsize     Mammal

[5 rows x 17 columns]

In [ ]:
transacs_class_Mammal = []
for i in range(0,len(class_Mammal)):
  transacs_class_Mammal.append([str(class_Mammal.values[i,j]) for j in range(1,16)])
transacs_class_Mammal

In [ ]:
asso_class_Mam = list(apriori(transacs_class_Mammal,min_support = 0.95, min_confidence = 0.9))
asso_class_Mam

## ถ้าสัตว์ประเภท Mammal 
- มีกระดูกสันหลัง จะมีโอกาสที่จะมีฟัน นม และมีหาง อยู่ 97.56%
- มีกระดูกสันหลังและมีนมด้วย จะมีโอกาสที่จะมีฟันและหาง อยู่ 97.56%
- มีกระดูกสันหลัง ฟัน และนม จะมีโอกาสที่จะมีหาง อยู่ 100%
- lift เท่ากับ 1 คือ ลักษณะทั้งสองมีความสัมพันธ์กัน

## Association ของสัตว์ประเภท Fish

In [ ]:
class_Fish = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Fish']
class_Fish.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
2      nohair     nofeathers       eggs  ...     nodomestic     nocatsize       Fish
7      nohair     nofeathers       eggs  ...       domestic     nocatsize       Fish
8      nohair     nofeathers       eggs  ...     nodomestic     nocatsize       Fish
12     nohair     nofeathers       eggs  ...     nodomestic     nocatsize       Fish
18     nohair     nofeathers       eggs  ...     nodomestic       catsize       Fish

[5 rows x 17 columns]

In [ ]:
transacs_class_Fish = []
for i in range(0,len(class_Fish)):
  transacs_class_Fish.append([str(class_Fish.values[i,j]) for j in range(1,16)])
transacs_class_Fish

In [ ]:
asso_class_Fish = list(apriori(transacs_class_Fish,min_support = 0.95, min_confidence = 0.9))
asso_class_Fish

## Association ของสัตว์ประเภท Bird

In [ ]:
class_Bird = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Bird']
class_Bird.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
11     nohair       feathers       eggs  ...       domestic     nocatsize       Bird
16     nohair       feathers       eggs  ...     nodomestic     nocatsize       Bird
20     nohair       feathers       eggs  ...       domestic     nocatsize       Bird
21     nohair       feathers       eggs  ...     nodomestic     nocatsize       Bird
23     nohair       feathers       eggs  ...     nodomestic       catsize       Bird

[5 rows x 17 columns]

In [ ]:
transacs_class_Bird = []
for i in range(0,len(class_Bird)):
  transacs_class_Bird.append([str(class_Bird.values[i,j]) for j in range(1,16)])
transacs_class_Bird

In [ ]:
asso_class_Bird = list(apriori(transacs_class_Bird,min_support = 0.95, min_confidence = 0.9))
asso_class_Bird

## Association ของสัตว์ประเภท Reptile(สัตว์เลื้อยคลาน)

In [ ]:
class_Reptile = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Reptile']
class_Reptile.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
62     nohair     nofeathers       eggs  ...     nodomestic     nocatsize    Reptile
76     nohair     nofeathers     noeggs  ...     nodomestic     nocatsize    Reptile
80     nohair     nofeathers       eggs  ...     nodomestic     nocatsize    Reptile
90     nohair     nofeathers       eggs  ...     nodomestic       catsize    Reptile
91     nohair     nofeathers       eggs  ...     nodomestic     nocatsize    Reptile

[5 rows x 17 columns]

In [ ]:
transacs_class_Reptile = []
for i in range(0,len(class_Reptile)):
  transacs_class_Reptile.append([str(class_Reptile.values[i,j]) for j in range(1,16)])
transacs_class_Reptile

In [ ]:
asso_class_Reptile = list(apriori(transacs_class_Reptile,min_support = 0.95, min_confidence = 0.9))
asso_class_Reptile

[RelationRecord(items=frozenset({'backbone'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'backbone'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'noairborne'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'noairborne'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'nodomestic'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nodomestic'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'nofeathers'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nofeathers'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'nofins'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nofins'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'nomilk'}), support=1.0, ordered_s

## ถ้าสัตว์ประเภท Reptile
- ถ้ามีหาง จะไม่มีปีก อยู่ 100%
- lift เท่ากับ 1 คือ ลักษณะทั้งสองมีความสัมพันธ์กัน

## Association ของสัตว์ประเภท Amphibian(สัตว์สะเทินน้ำสะเทินบก)

In [ ]:
class_Amphibian = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Amphibian']
class_Amphibian.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
25     nohair     nofeathers       eggs  ...     nodomestic     nocatsize  Amphibian
26     nohair     nofeathers       eggs  ...     nodomestic     nocatsize  Amphibian
52     nohair     nofeathers       eggs  ...     nodomestic     nocatsize  Amphibian
89     nohair     nofeathers       eggs  ...     nodomestic     nocatsize  Amphibian

[4 rows x 17 columns]

In [ ]:
transacs_class_Amphibian = []
for i in range(0,len(class_Amphibian)):
  transacs_class_Amphibian.append([str(class_Amphibian.values[i,j]) for j in range(1,16)])
transacs_class_Amphibian

In [ ]:
asso_class_Amphibian = list(apriori(transacs_class_Amphibian,min_support = 0.95, min_confidence = 0.9))
asso_class_Amphibian

[RelationRecord(items=frozenset({'4legs'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'4legs'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'aquatic'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'aquatic'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'backbone'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'backbone'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'breathes'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'breathes'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'eggs'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'eggs'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'noairborne'}), support=1.0, ordered_statistics=[OrderedSt

## ถ้าสัตว์ประเภท Amphibian(สัตว์สะเทินน้ำสะเทินบก)
- ถ้ามีหาง มีกระดูกสันหลัง จะไม่มีปีก อยู่ 100%
- lift เท่ากับ 1 คือ ลักษณะทั้งสองมีความสัมพันธ์กัน

## Association ของสัตว์ประเภท Bug(แมลง)

In [ ]:
class_Bug = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Bug']
class_Bug.head()

hair_group feathers_group eggs_group  ... domestic_group catsize_group Class_Type
24     nohair     nofeathers       eggs  ...     nodomestic     nocatsize        Bug
30     nohair     nofeathers       eggs  ...     nodomestic     nocatsize        Bug
39       hair     nofeathers       eggs  ...       domestic     nocatsize        Bug
40       hair     nofeathers       eggs  ...     nodomestic     nocatsize        Bug
42     nohair     nofeathers       eggs  ...     nodomestic     nocatsize        Bug

[5 rows x 17 columns]

In [ ]:
transacs_class_Bug = []
for i in range(0,len(class_Bug)):
  transacs_class_Bug.append([str(class_Bug.values[i,j]) for j in range(1,16)])
transacs_class_Bug

In [ ]:
asso_class_Bug = list(apriori(transacs_class_Bug,min_support = 0.95, min_confidence = 0.9))
asso_class_Bug

[RelationRecord(items=frozenset({'6legs'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'6legs'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'breathes'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'breathes'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'eggs'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'eggs'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'noaquatic'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'noaquatic'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'nobackbone'}), support=1.0, ordered_statistics=[OrderedStatistic(items_base=frozenset(), items_add=frozenset({'nobackbone'}), confidence=1.0, lift=1.0)]),
 RelationRecord(items=frozenset({'nocatsize'}), support=1.0, ordered_statistics=[Or

## ถ้าสัตว์ประเภท Bug(แมลง)
- ถ้ามีการหายใจทางจมูก มี 6 ขา มีไข่ จะไม่ใบหู อยู่ 100%
- lift เท่ากับ 1 คือ ลักษณะทั้งสองมีความสัมพันธ์กัน

## Association ของสัตว์ประเภท Invertebrate(สัตว์ไม่มีกระดูกสันหลัง)

In [ ]:
class_Invertebrate = class_z_merged_dr[class_z_merged_dr['Class_Type']=='Invertebrate']
class_Invertebrate.head()

hair_group feathers_group  ... catsize_group    Class_Type
13     nohair     nofeathers  ...     nocatsize  Invertebrate
14     nohair     nofeathers  ...     nocatsize  Invertebrate
15     nohair     nofeathers  ...     nocatsize  Invertebrate
46     nohair     nofeathers  ...     nocatsize  Invertebrate
53     nohair     nofeathers  ...       catsize  Invertebrate

[5 rows x 17 columns]

In [ ]:
transacs_class_Invertebrate = []
for i in range(0,len(class_Invertebrate)):
  transacs_class_Invertebrate.append([str(class_Invertebrate.values[i,j]) for j in range(1,16)])
transacs_class_Invertebrate

In [ ]:
asso_class_Invertebrate = list(apriori(transacs_class_Invertebrate,min_support = 0.95, min_confidence = 0.9))
asso_class_Invertebrate

## ถ้าสัตว์ประเภท Invertebrate(สัตว์ไม่มีกระดูกสันหลัง)
- จะไม่มีนม ไม่มีครีบ ไม่มีปีก ไม่มีฟัน อยู่ 100%
- lift เท่ากับ 1 คือ ลักษณะทั้งสองมีความสัมพันธ์กัน

# K-Nearest Neighbors
##เพื่อทำนาย Class ของสัตว์ โดยทำนายลักษณทั้ง 16 ลักษณะ

### เรียกตารางที่ต้องการใช้ออกมาให้อยู่ในตัวแปร animal

In [ ]:
animal = zoo_type_df  
animal.head()

animal_name  hair  feathers  ...  tail_group  domestic_group  catsize_group
0    aardvark     1         0  ...        tail      nodomestic        catsize
1    antelope     1         0  ...        tail      nodomestic        catsize
2        bass     0         0  ...        tail      nodomestic      nocatsize
3        bear     1         0  ...        tail      nodomestic        catsize
4        boar     1         0  ...        tail      nodomestic        catsize

[5 rows x 34 columns]

### ทำการตรวจสอบค่า Missing

In [ ]:
#ตรวจสอบว่ามีค่า null หรือไม่
animal.isnull().any()

animal_name       False
hair              False
feathers          False
eggs              False
milk              False
airborne          False
aquatic           False
predator          False
toothed           False
backbone          False
breathes          False
venomous          False
fins              False
legs              False
tail              False
domestic          False
catsize           False
class_type        False
hair_group        False
feathers_group    False
eggs_group        False
milk_group        False
airborne_group    False
aquatic_group     False
predator_group    False
toothed_group     False
backbone_group    False
breathes_group    False
venomous_group    False
fins_group        False
legs_group        False
tail_group        False
domestic_group    False
catsize_group     False
dtype: bool

### - ร่วมตาราง animal และตาราง class เข้าด้วยกัน โดยกำหนดตาราง class_type_df ให้อยู่ในตัวแปรที่ชื่อ ani_class 
### - หลังจากนั้นทำการตั้งชื่อตัวแปร df เพื่อ merge ตาราง animal และ ani_class เข้าด้วยกันโดยมีคีย์ คือ class_type และ Class_Number

In [ ]:
ani_class = class_type_df 
df = pd.merge(animal,ani_class,how='left',left_on='class_type',right_on='Class_Number')
df.head()

animal_name  ...                                        Animal_Name
0    aardvark  ...  aardvark, antelope, bear, boar, buffalo, calf,...
1    antelope  ...  aardvark, antelope, bear, boar, buffalo, calf,...
2        bass  ...  bass, carp, catfish, chub, dogfish, haddock, h...
3        bear  ...  aardvark, antelope, bear, boar, buffalo, calf,...
4        boar  ...  aardvark, antelope, bear, boar, buffalo, calf,...

[5 rows x 38 columns]

In [ ]:
N_df = class_type_df[['Class_Number','Class_Type']]
N_df

Class_Number    Class_Type
0             1        Mammal
1             2          Bird
2             3       Reptile
3             4          Fish
4             5     Amphibian
5             6           Bug
6             7  Invertebrate

In [ ]:
from sklearn.model_selection import train_test_split

### ทำการแบ่ง train และ test ออกเป็น 80/20 

### - กำหนดค่า X โดยเรียกใช้ตาราง animal และใช้คำสั่ง .iloc ให้เอาทุกแถวตั้งแต่คอลัมที่ 1 ถึง คอลัมที่ 17 
### - กำหนดค่า y โดยเรียกใช้ตาราง animal และใช้คำสั่ง .iloc ให้เอาทุกแถวของคอลัมที่ 17 
### - เราจะส่ง X และ y ไปให้ฟังก์ชั่น train_test_split นี้ พร้อมกับกำหนด 
*   test_size คือ ขนาดอัตราส่วนของข้อมูลกลุ่ม test ต่อข้อมูลกลุ่ม train ในที่นี้เท่ากับ 0.2 
*  random_state คือ ค่าที่กำหนดการ random กลุ่มข้อมูล จะเป็นเลขจำนวนเต็ม ถ้ากำหนดเลขเดิม ผลการ split ก็เหมือนเดิม
*  stratify คือ การกำหนดการกระจายของข้อมูลที่ split ให้มีการกระจายเหมือน original dataset



In [ ]:
X = df.iloc[:,1:17] 
y = df.iloc[:,17]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=1, stratify=y)

In [ ]:
X_train.shape

(80, 16)

In [ ]:
X_test.shape

(21, 16)

In [ ]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import cross_val_score

### Define นิยามโมเดล เช่น กำหนดค่า K 

In [ ]:
myKNN = KNeighborsClassifier(n_neighbors=3) 

### ทำการ Train (fit) เพื่อสร้างโมเดล

In [ ]:
myKNN.fit(X_train,y_train)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=None, n_neighbors=3, p=2,
                     weights='uniform')

### ทำการ Test โดยใช้คำสั่ง .predict นำข้อมูลจาก X_test 

In [ ]:
myKNN.predict(X_test)

array([5, 3, 1, 1, 6, 4, 1, 6, 1, 2, 1, 1, 1, 2, 7, 2, 4, 7, 1, 2, 4])

In [ ]:
N_df[N_df['Class_Number'] == 5]

### ใช้คำสั่ง .predict_proba เป็นการคำนวณความน่าจะเป็นว่า ข้อมูลลักษณะของสัตว์ที่นำเข้าไปในโมเดลนั้นจะอยู่ประเภทไหนกี่เปอร์เซ็นต์

In [ ]:
myKNN.predict_proba(X_test)

array([[0.        , 0.        , 0.        , 0.        , 1.        ,
        0.        , 0.        ],
       [0.        , 0.        , 0.66666667, 0.33333333, 0.        ,
        0.        , 0.        ],
       [0.66666667, 0.33333333, 0.        , 0.        , 0.        ,
        0.        , 0.        ],
       [1.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        ],
       [0.        , 0.        , 0.        , 0.        , 0.        ,
        1.        , 0.        ],
       [0.        , 0.        , 0.        , 1.        , 0.        ,
        0.        , 0.        ],
       [1.        , 0.        , 0.        , 0.        , 0.        ,
        0.        , 0.        ],
       [0.        , 0.        , 0.        , 0.        , 0.        ,
        1.        , 0.        ],
       [0.66666667, 0.        , 0.        , 0.33333333, 0.        ,
        0.        , 0.        ],
       [0.        , 1.        , 0.        , 0.        , 0.        ,
        0.        , 0. 

### ตรวจสอบความแม่นยำของโมเดล ว่าสามารถจำแจกประเภทของสัตว์ ได้ที่ความแม่นยำกี่เปอร์เซ็นต์

In [ ]:
cross_val_score(myKNN, X_train, y_train, cv=10).mean()

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 3 members, which is less than n_splits=10.
  % (min_groups, self.n_splits)), UserWarning)


0.9125